In [1]:
# Hier werden alle verwendeten Pythonmodule importiert
import Datenbank
import Import
import importlib
import Koordinatentransformationen
import sqlite3

In [2]:
importlib.reload(Import)
# Anlegen der Datenbank, wenn nicht vorhanden
pfad_datenbank = r"Campusnetz.db"
Datenbank.Datenbank_anlegen(pfad_datenbank)

# Import vervollständigen
imp = Import.Import(pfad_datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)

In [3]:
# Import der Koordinatendatei(en) vom Tachymeter
pfad_datei = r"Daten\campsnetz_final_koordinaten.csv"
imp.import_koordinaten_lh_tachymeter(pfad_datei)

Der Import der Näherungskoordinaten wurde erfolgreich abgeschlossen


In [4]:
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)
# Transformationen in ETRS89 / DREF91 Realisierung 2025
print(db_zugriff.get_koordinaten("naeherung_lh"))

{'10009': Matrix([
[1000.0],
[2000.0],
[ 100.0]]), '10006': Matrix([
[   1000.0],
[2032.6863],
[  99.5825]]), '10010': Matrix([
[1011.8143],
[1973.3252],
[  99.9259]]), '10018': Matrix([
[1008.5759],
[ 1942.762],
[ 100.2553]]), '10008': Matrix([
[979.7022],
[1991.401],
[  99.732]]), '10005': Matrix([
[ 966.5154],
[2014.6496],
[    99.72]]), '10003': Matrix([
[ 908.4312],
[1996.1248],
[  99.7403]]), '10004': Matrix([
[ 954.1536],
[2021.6822],
[  99.4916]]), '10007': Matrix([
[ 921.7481],
[1973.6201],
[  99.9176]]), '10001': Matrix([
[ 833.9439],
[1978.3737],
[  99.8946]]), '10002': Matrix([
[ 875.9684],
[1998.5174],
[  99.5867]]), '100016': Matrix([
[ 928.2783],
[1944.0082],
[ 100.0459]]), '10011': Matrix([
[ 908.4308],
[1996.1277],
[  99.7822]]), '10011a': Matrix([
[844.9567],
[1891.157],
[ 99.8117]]), '10026': Matrix([
[1020.0059],
[1913.8703],
[ 100.3059]]), '10027': Matrix([
[1016.9451],
[1866.2914],
[ 100.3251]]), '10043': Matrix([
[1031.2077],
[1822.4739],
[ 100.3035]]), '10044': 

In [5]:
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)
# Transformationen in ETRS89 / DREF91 Realisierung 2025
print(db_zugriff.get_koordinaten("naeherung_us"))

{}


In [6]:
# ToDo: Sobald GNSS vorliegend Koordinaten im ETRS89 / DREF 91 (2025) daraus berechnen!
liste_koordinaten_naeherung_us_alt = {
    10001: (3794874.98408291, 546741.751930012, 5079995.3838),
    10002: (3794842.53340714, 546726.907150697, 5080039.8778),
    10008: (3794757.41294192, 546742.822339098, 5080107.3198),
    10012: (3794827.11937161, 546801.412652168, 5080028.5852),
    10026: (3794727.06042449, 546823.571170112, 5080134.2029),
    10028: (3794862.91900719, 546904.943464041, 5079920.8994),
    10037: (3794774.14751515, 546955.423068316, 5079960.9426),
    10044: (3794725.78597473, 546954.557211544, 5080009.9234),
    10054: (3794852.07416848, 547094.399826613, 5079715.1737),
    10059: (3794710.34348443, 547075.630380075, 5080119.6491),
}

liste_koordinaten_naeherung_us_V2 = {
    10001: (3794874.984, 546741.752, 5080029.990),
    10002: (3794842.533, 546726.907, 5080071.133),
    10008: (3794757.413, 546742.822, 5080135.400),
    10012: (3794827.119, 546801.413, 5080065.404),
    10026: (3794727.060, 546823.571, 5080179.951),
    10028: (3794862.919, 546904.943, 5079963.214),
    10037: (3794774.148, 546955.423, 5080040.520),
    10044: (3794725.786, 546954.557, 5080084.411),
    10054: (3794852.074, 547094.400, 5079771.845),
    10059: (3794710.343, 547075.630, 5080153.653),
}

liste_koordinaten_naeherung_us = {
    10001: (3794874.984, 546741.752, 5080029.990),
    10002: (3794842.533, 546726.907, 5080071.133),
    10037: (3794774.148, 546955.423, 5080040.520),
    10044: (3794725.786, 546954.557, 5080084.411),
}


con = sqlite3.connect(pfad_datenbank)
cursor = con.cursor()
sql = """
UPDATE Netzpunkte
SET naeherungx_us = ?, naeherungy_us = ?, naeherungz_us = ?
WHERE punktnummer = ?
"""
for punktnummer, (x, y, z) in liste_koordinaten_naeherung_us.items():
    cursor.execute(sql, (x, y, z, punktnummer))
con.commit()
cursor.close()
con.close()

In [10]:
# ToDo: Sobald GNSS-Daten vorliegen und die Berechnungen richtig sind, aufräumen!!!

importlib.reload(Koordinatentransformationen)
trafos = Koordinatentransformationen.Transformationen(pfad_datenbank)


import numpy as np

import itertools
import numpy as np
import sympy as sp

db = Datenbank.Datenbankzugriff(pfad_datenbank)
dict_ausgangssystem = db.get_koordinaten("naeherung_lh", "Dict")
dict_zielsystem = db.get_koordinaten("naeherung_us", "Dict")

gemeinsame_punktnummern = sorted(set(dict_ausgangssystem.keys()) & set(dict_zielsystem.keys()))
anzahl_gemeinsame_punkte = len(gemeinsame_punktnummern)

liste_punkte_ausgangssystem = [dict_ausgangssystem[i] for i in gemeinsame_punktnummern]
liste_punkte_zielsystem = [dict_zielsystem[i] for i in gemeinsame_punktnummern]

def dist(a, b):
    return float((a - b).norm())

print("d(p2,p1)=", dist(liste_punkte_ausgangssystem[1], liste_punkte_ausgangssystem[0]))
print("d(P2,P1)=", dist(liste_punkte_zielsystem[1], liste_punkte_zielsystem[0]))
print("m0 ~", dist(liste_punkte_zielsystem[1], liste_punkte_zielsystem[0]) /
               dist(liste_punkte_ausgangssystem[1], liste_punkte_ausgangssystem[0]))


def dist(a, b):
    return float((a - b).norm())

ratios = []
pairs = list(itertools.combinations(range(len(liste_punkte_ausgangssystem)), 2))

for i, j in pairs:
    d_loc = dist(liste_punkte_ausgangssystem[i], liste_punkte_ausgangssystem[j])
    d_ecef = dist(liste_punkte_zielsystem[i], liste_punkte_zielsystem[j])
    if d_loc > 1e-6:
        ratios.append(d_ecef / d_loc)

print("Anzahl Ratios:", len(ratios))
print("min/mean/max:", min(ratios), sum(ratios)/len(ratios), max(ratios))
print("std:", float(np.std(ratios)))

S_loc = sum(liste_punkte_ausgangssystem, sp.Matrix([0,0,0])) / anzahl_gemeinsame_punkte
S_ecef = sum(liste_punkte_zielsystem, sp.Matrix([0,0,0])) / anzahl_gemeinsame_punkte

print("S_loc:", S_loc)
print("S_ecef:", S_ecef)
print("Delta:", (S_ecef - S_loc).evalf(6))


def dist(a, b):
    return float((a - b).norm())

n = len(liste_punkte_ausgangssystem)

scores = []
for i in range(n):
    d_loc = []
    d_ecef = []
    for j in range(n):
        if i == j:
            continue
        d_loc.append(dist(liste_punkte_ausgangssystem[i], liste_punkte_ausgangssystem[j]))
        d_ecef.append(dist(liste_punkte_zielsystem[i], liste_punkte_zielsystem[j]))

    d_loc = np.array(d_loc)
    d_ecef = np.array(d_ecef)

    # Verhältnisvektor; robust gegen Nullschutz
    r = d_ecef / np.where(d_loc == 0, np.nan, d_loc)

    # Streuung der Ratios für Punkt i
    score = np.nanstd(r)
    scores.append(score)

for pn, sc in sorted(zip(gemeinsame_punktnummern, scores), key=lambda x: -x[1]):
    print(pn, round(sc, 4))



transformationsparameter = trafos.Helmerttransformation_Euler_Transformationsparameter_berechne()

d(p2,p1)= 46.60388451996242
d(P2,P1)= 54.462720048072995
m0 ~ 1.1686304823956102
Anzahl Ratios: 6
min/mean/max: 0.9679784506116116 1.0266943302085056 1.1686304823956102
std: 0.07473161831852519
S_loc: Matrix([[925.528400000000], [1883.39492500000], [100.005775000000]])
S_ecef: Matrix([[3794804.36275000], [546844.659750000], [5080056.51350000]])
Delta: Matrix([[3.79388e+6], [544961.], [5.07996e+6]])
10001 0.0936
10002 0.0873
10044 0.0527
10037 0.0477
Anzahl gemeinsame Punkte: 4

Erste Zielpunkte:
10001 [3794874.984, 546741.752, 5080029.99]
10002 [3794842.533, 546726.907, 5080071.133]
10037 [3794774.148, 546955.423, 5080040.52]
10044 [3794725.786, 546954.557, 5080084.411]

Erste Ausgangspunkte:
10001 [833.9439, 1978.3737, 99.8946]
10002 [875.9684, 1998.5174, 99.5867]
10037 [966.2253, 1774.2051, 99.9957]
10044 [1025.976, 1782.4835, 100.5461]
min/mean/max: 0.9679784506116116 1.0266943302085056 1.1686304823956102
R ist Orthonormal!
Iteration Nr.1 abgeschlossen
Matrix([[-85.7], [-61.5], [188

In [20]:
importlib.reload(Koordinatentransformationen)
trafos = Koordinatentransformationen.Transformationen(pfad_datenbank)

koordinaten_transformiert = trafos.Helmerttransformation(transformationsparameter)
print(koordinaten_transformiert)

{'100': Matrix([
[3794775.24129598],
[547003.784566026],
[5080016.88582709]]), '100016': Matrix([
[3794804.40667566],
[546789.942078133],
[5080079.63649543]]), '10003': Matrix([
[3794820.51175889],
[546738.121545569],
[5080085.66027136]]), '10004': Matrix([
[3794787.68039096],
[546724.355539902],
[5080122.57197924]]), '10005': Matrix([
[3794778.52744143],
[546733.440239574],
[5080127.82709672]]), '10006': Matrix([
[3794754.48961774],
[546723.992131817],
[ 5080154.6491784]]), '10007': Matrix([
[   3794810.10603],
[546761.510609237],
[ 5080086.0020765]]), '10008': Matrix([
[3794768.08506589],
[546757.433496855],
[ 5080127.7145515]]), '10009': Matrix([
[3794753.66298807],
[546753.936763795],
[ 5080143.3866772]]), '10010': Matrix([
[3794744.05628981],
[546780.742811981],
[ 5080141.1636738]]), '10011': Matrix([
[3794820.53929209],
[546738.130781189],
[ 5080085.6893844]]), '10011a': Matrix([
[3794863.58049222],
[546820.559672293],
[5080009.68904121]]), '10012': Matrix([
[3794827.81056398],
[

In [24]:
importlib.reload(Datenbank)
db_zugriff = Datenbank.Datenbankzugriff(pfad_datenbank)

db_zugriff.set_koordinaten(koordinaten_transformiert, "naeherung_us")